In [1]:
import org.apache.spark.sql.SQLContext
import org.apache.spark.sql.types.{StructType, StructField, StringType, DoubleType};
import com.databricks.spark.xml._

val sqlContext = new SQLContext(sc)
import sqlContext.implicits._
sqlContext.sql("set spark.sql.caseSensitive=true") 
spark.sparkContext.uiWebUrl

Waiting for a Spark session to start...

sqlContext = org.apache.spark.sql.SQLContext@194187e1


Some(http://iuni2:4040)

In [2]:
//val sqlContext = new SQLContext(sc)
val df = sqlContext.read
  .format("com.databricks.spark.xml")
  .option("rowTag", "REC")
  //.schema(customSchema)
  .load("/WoSraw/WoS2019/xmlRaw/*.xml.gz")

df.show(2)
df.printSchema()

Name: org.apache.spark.SparkException
Message: Job 0 cancelled as part of cancellation of all jobs
StackTrace:   at org.apache.spark.scheduler.DAGScheduler.org$apache$spark$scheduler$DAGScheduler$$failJobAndIndependentStages(DAGScheduler.scala:1890)
  at org.apache.spark.scheduler.DAGScheduler.handleJobCancellation(DAGScheduler.scala:1825)
  at org.apache.spark.scheduler.DAGScheduler$$anonfun$doCancelAllJobs$1.apply$mcVI$sp(DAGScheduler.scala:833)
  at org.apache.spark.scheduler.DAGScheduler$$anonfun$doCancelAllJobs$1.apply(DAGScheduler.scala:833)
  at org.apache.spark.scheduler.DAGScheduler$$anonfun$doCancelAllJobs$1.apply(DAGScheduler.scala:833)
  at scala.collection.mutable.HashSet.foreach(HashSet.scala:78)
  at org.apache.spark.scheduler.DAGScheduler.doCancelAllJobs(DAGScheduler.scala:833)
  at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.doOnReceive(DAGScheduler.scala:2083)
  at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.onReceive(DAGScheduler.scala:2060)
 

In [4]:
import org.apache.spark.sql.SaveMode
df.write.mode(SaveMode.Overwrite)
.parquet("/WoSraw/WoS2019/parquet")
//WoS2.describe().filter($"summary" === "count").show

In [2]:
val WoS = spark.read.format("parquet").load("/WoSraw/WoS2019/parquet/*.parquet")

val WoS2 = WoS.select("UID","dynamic_data.cluster_related.identifiers.identifier","static_data.summary.doctypes.doctype",
                      "static_data.summary.names.name","static_data.summary.titles","static_data.summary.conferences.conference",
                      "static_data.fullrecord_metadata.addresses.address_name", "static_data.fullrecord_metadata.reprint_addresses",
                      "static_data.fullrecord_metadata.abstracts.abstract.abstract_text",
                      "static_data.fullrecord_metadata.keywords.keyword","static_data.fullrecord_metadata.references.reference",
                      "static_data.contributors.contributor","static_data.summary.EWUID",
                      "static_data.summary.pub_info","static_data.summary.publishers","static_data.fullrecord_metadata.fund_ack")
WoS2.printSchema

root
 |-- UID: string (nullable = true)
 |-- identifier: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- _VALUE: string (nullable = true)
 |    |    |-- _type: string (nullable = true)
 |    |    |-- _value: string (nullable = true)
 |-- doctype: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- name: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- _addr_no: string (nullable = true)
 |    |    |-- _orcid_id_tr: string (nullable = true)
 |    |    |-- _r_id_tr: string (nullable = true)
 |    |    |-- _reprint: string (nullable = true)
 |    |    |-- _role: string (nullable = true)
 |    |    |-- _seq_no: long (nullable = true)
 |    |    |-- display_name: string (nullable = true)
 |    |    |-- email_addr: string (nullable = true)
 |    |    |-- first_name: string (nullable = true)
 |    |    |-- full_name: string (nullable = true)
 |    |    |-- last_name: string (nullable = true)
 

WoS = [UID: string, _r_id_disclaimer: string ... 14 more fields]
WoS2 = [UID: string, identifier: array<struct<_VALUE:string,_type:string,_value:string>> ... 14 more fields]


[UID: string, identifier: array<struct<_VALUE:string,_type:string,_value:string>> ... 14 more fields]

In [64]:
WoS2.write.mode(SaveMode.Overwrite).json("/WoSraw/json")

In [58]:
import org.apache.spark.sql.functions._

val WoS3 = WoS2.select("UID", "pub_info._pubtype", "pub_info._pubyear", "fund_ack.fund_text", "titles", "reprint_addresses",
                       "identifier", "name","publishers.publisher.names.name.full_name","address_name.address_spec.full_address","address_name.address_spec.organizations")
val WoSIU = WoS3.withColumn("allAddresses", array_join($"full_address", "|")).filter($"allAddresses".contains("Indiana Univ")).cache()
WoSIU.describe().filter($"summary" === "count").show

+-------+------+--------+--------+---------+------------+
|summary|   UID|_pubtype|_pubyear|full_name|allAddresses|
+-------+------+--------+--------+---------+------------+
|  count|133767|  133767|  133767|   133766|      133767|
+-------+------+--------+--------+---------+------------+



WoS3 = [UID: string, _pubtype: string ... 9 more fields]
WoSIU = [UID: string, _pubtype: string ... 10 more fields]


[UID: string, _pubtype: string ... 10 more fields]

In [59]:
val WoSIU2 = WoSIU.filter(($"_pubyear"===2018||$"_pubyear"===2019))//&&$"full_name".contains("ELSEVIER"))
//WoSIU2.describe().filter($"summary" === "count").show
val WoSIU3 = WoSIU2.withColumn("FX", array_join($"fund_text.p", ".")).withColumn("RPAddresses", array_join($"reprint_addresses.address_name.address_spec.full_address", "|"))
WoSIU3.show

+-------------------+--------+--------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|                UID|_pubtype|_pubyear|           fund_text|              titles|   reprint_addresses|          identifier|                name|           full_name|        full_address|       organizations|        allAddresses|                  FX|         RPAddresses|
+-------------------+--------+--------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|WOS:000418232300001| Journal|    2018|[[We thank Drs. K...|[6, [[HUMAN GENE ...|[1, [[[1, Birming...|[[, accession_no,...|[[1 2,,,, author,...|MARY ANN LIEBERT,...|[Indiana Univ Sch...|[

WoSIU2 = [UID: string, _pubtype: string ... 10 more fields]
WoSIU3 = [UID: string, _pubtype: string ... 12 more fields]


[UID: string, _pubtype: string ... 12 more fields]

In [60]:
import scala.util.Try
import org.apache.hadoop.fs._
import org.apache.spark.sql.Row

def getTitle(_type: String) = { 
  udf((row: Seq[Row]) =>
    row.map(r => (r.getString(0), r.getString(1), r.getString(2)))
      .find { case (_, _, s) => s == _type}
      .map(_._1)
      .orElse(None)
  )
}
val WoSIU4 = WoSIU3.withColumn("journal", when(col("titles.title").isNotNull, getTitle("source")($"titles.title")).otherwise(lit(null))).cache()
WoSIU4.show()

+-------------------+--------+--------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|                UID|_pubtype|_pubyear|           fund_text|              titles|   reprint_addresses|          identifier|                name|           full_name|        full_address|       organizations|        allAddresses|                  FX|         RPAddresses|             journal|
+-------------------+--------+--------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|WOS:000418232300001| Journal|    2018|[[We thank Drs. K...|[6, [[HUMAN GENE ...|[1, [[[1, Birming...|[[, accession_no,...|[

WoSIU4 = [UID: string, _pubtype: string ... 13 more fields]


getTitle: (_type: String)org.apache.spark.sql.expressions.UserDefinedFunction


[UID: string, _pubtype: string ... 13 more fields]

In [61]:
//WoSIU4.write.mode(SaveMode.Overwrite).parquet("/WoSraw/WoS2019/IUpapersExtract")
//val WoSIU4b = spark.read.format("parquet").load("/WoSraw/WoS2019/IUpapersExtract/*.parquet")
val WoSIU5 = WoSIU4.withColumn("title", when(col("titles.title").isNotNull, getTitle("item")($"titles.title")).otherwise(lit(null)))
WoSIU5.show

+-------------------+--------+--------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|                UID|_pubtype|_pubyear|           fund_text|              titles|   reprint_addresses|          identifier|                name|           full_name|        full_address|       organizations|        allAddresses|                  FX|         RPAddresses|             journal|               title|
+-------------------+--------+--------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|WOS:000418232300001| Journal|    2018|[[We thank Drs. K...|[

WoSIU5 = [UID: string, _pubtype: string ... 14 more fields]


[UID: string, _pubtype: string ... 14 more fields]

In [62]:
def getID(_type: String) = {
  udf((row: Seq[Row]) =>
    row.map(r => (r.getString(0), r.getString(1), r.getString(2)))
      .find { case (_, s, _) => s == _type}
      .map(_._3)
      .orElse(None)
  )
}


val WoSIU6 = WoSIU5.withColumn("doi", when(col("identifier").isNotNull, getID("doi")($"identifier")).otherwise(lit(null)))
.withColumn("issn", when(col("identifier").isNotNull, getID("issn")($"identifier")).otherwise(lit(null)))
.withColumn("eissn", when(col("identifier").isNotNull, getID("eissn")($"identifier")).otherwise(lit(null)))
//.select("UID","doi","issn","eissn").filter($"doi" =!= "null").show
WoSIU6.describe().filter($"summary" === "count").show

+-------+-----+--------+--------+---------+------------+----+-----------+-------+-----+-----+-----+-----+
|summary|  UID|_pubtype|_pubyear|full_name|allAddresses|  FX|RPAddresses|journal|title|  doi| issn|eissn|
+-------+-----+--------+--------+---------+------------+----+-----------+-------+-----+-----+-----+-----+
|  count|16464|   16464|   16464|    16464|       16464|8413|      13949|  16464|16464|13233|15797|13375|
+-------+-----+--------+--------+---------+------------+----+-----------+-------+-----+-----+-----+-----+



WoSIU6 = [UID: string, _pubtype: string ... 17 more fields]


getID: (_type: String)org.apache.spark.sql.expressions.UserDefinedFunction


[UID: string, _pubtype: string ... 17 more fields]

In [70]:
val WoSIU7 = WoSIU6.withColumn("RPnameList",flatten($"reprint_addresses.address_name.names.name"))
                   //.withColumn("orgList",flatten($"organizations"))
val WoSIU8 = WoSIU7//.withColumn("reprintFlag", array_position($"name._reprint", "Y"))
.select("UID","_pubtype","_pubyear","eissn","issn","doi","title","journal","full_name","FX",
"reprint_addresses._count","RPnameList.last_name","RPAddresses","name.display_name","name._reprint","name._addr_no","allAddresses")
.toDF("WoSid","PT","PY","EI","SN","DI","TI","SO","PU","FX","RPcount","RPname","RP","authors","RPflag","author-address","C1")

val WoSIU9 = WoSIU8.withColumn("AU", array_join($"authors", "|")).withColumn("RPnames", array_join($"RPname", "|"))
                   .withColumn("RPflags", array_join($"RPflag", "|", "N")) //array_join(array, delimiter, nullReplacement(optional)) 
                   //.withColumn("C1flags", array_join($"C1flag",";"))
                   .withColumn("AU-C1-map", array_join($"author-address","|"))
WoSIU9.show(false)

+-------------------+-------+----+---------+---------+----------------------------------+----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+-----------------------------------------------------------------+-----------------------------+------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

|WOS:000414522900001|Journal|2018|1557-9042|0897-7151|10.1089/neu.2017.5203             |Traumatic Brain Injury in hTau Model Mice: Enhanced Acute Macrophage Response and Altered Long-Term Recovery                                                                                              |JOURNAL OF NEUROTRAUMA                                           |MARY ANN LIEBERT, INC        |This work was supported by the Department of Defense and National Institutes of Health (W81XWH-12-1-0629, BTL; R21NS077089, R01NS083704, R21NS093442, K.B.). We thank the Rodent Behavioral Core and the Flow Cytometry Core at the Lerner Research Institute within the Cleveland Clinic for technical advice and support. We thank Dr. Imad Najm for use of the fluid percussion device. Author contributions: O.K-C. designed, performed, and analyzed all experiments and wrote the manuscript; M.S. performed surgeries, TBIs, and flow cytometry experiments; S.P. analyzed all flow cytometry data and assisted in interpreta

|WOS:000417584100001|Journal|2018|1557-7708|1075-5535|10.1089/acm.2017.0241             |A Review Study on the Beneficial Effects of Baduanjin                                                                                                                                                     |JOURNAL OF ALTERNATIVE AND COMPLEMENTARY MEDICINE                |MARY ANN LIEBERT, INC        |This research project was supported by the Chinese National Social Science Foundation (15BTY088).                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

|WOS:000418128000001|Journal|2018|1557-9042|0897-7151|10.1089/neu.2017.5376             |Acute Changes in Plasma Total Tau Levels Are Independent of Subconcussive Head Impacts in College Football Players                                                                                        |JOURNAL OF NEUROTRAUMA                                           |MARY ANN LIEBERT, INC        |This work was supported by the Pennsylvania Athletic Trainers' Society research grant (to K. Kawata), generous support from Athole G. Jacobi, MD, and the Marianne Garman Burton Foundation for Caregivers (to D. Langford), and a seed grant from Temple University Office of the Vice Provost for Research (to D. Langford). Sponsors had no role in the design or execution of the study; collection, management, analysis, or interpretation of the data; preparation, review, or approval of the manuscript; or decision to submit the manuscript for publication.                                                             

|WOS:000439102000002|Journal|2018|1526-632X|0028-3878|10.1212/WNL.0000000000005213      |Attention-deficit/hyperactivity disorder medication and seizures                                                                                                                                          |NEUROLOGY                                                        |LIPPINCOTT WILLIAMS & WILKINS|This project was supported by NIMH grant R01MH102221, NIH grant T32HD07475, and NIDA grant K99DA040727. MarketScan is a registered trademark of Truven Health Analytics Inc.                                                                                                                                                                                                                                                                                                                                                                                                                                                        

...

|WOS:000428505700001|Journal|2018|2470-0029|2470-0010|10.1103/PhysRevD.97.052011        |Improved measurements of X-cJ -> Sigma(+) (Sigma)over-bar(-) and Sigma(0)(Sigma)over-bar(0) decays                                                                                                        |PHYSICAL REVIEW D                                                |AMER PHYSICAL SOC            |The BESIII Collaboration thanks the staff of BEPCII and the IHEP computing center for their strong support. This work is supported in part by National Key Basic Research Program of China under Contract No. 2015CB856700; National Natural Science Foundation of China (NSFC) under Contracts No. 11375204, No. 11505034, No. 11235011, No. 11335008, No. 11425524, No. 11625523, No. 11635010; the Chinese Academy of Sciences (CAS) Large-Scale Scientific Facility Program; the CAS Center for Excellence in Particle Physics (CCEPP); the Collaborative Innovation Center for Particles and Interactions (CICPI); Joint Large-

|WOS:000425840100038|Journal|2018|1549-9626|1549-9618|10.1021/acs.jctc.7b00702          |Multiscale Molecular Dynamics Approach to Energy Transfer in Nanomaterials                                                                                                                                |JOURNAL OF CHEMICAL THEORY AND COMPUTATION                       |AMER CHEMICAL SOC            |The authors acknowledge the National Science Foundation (NSF, DMREF-1533988) for support. The authors also acknowledge support by the IU College of Arts and Sciences via the Center for Theoretical and Computational Nanoscience and Lilly Endowment, Inc., through its support for the Indiana University Pervasive Technology Institute, and in part by the Indiana METACyt Initiative. The Indiana METACyt Initiative at IU is also supported in part by Lilly Endowment, Inc. The work done by J.M.E.D. was supported by the Colombian Administrative Department of Science, Technology, and Innovation - COLCIENCIAS - throug

|WOS:000425965600010|Journal|2018|1475-4533|0040-5574|10.1017/S0040557417000540         |Child Labor in the British Victorian Entertainment Industry, 1875-1914                                                                                                                                    |THEATRE SURVEY                                                   |CAMBRIDGE UNIV PRESS         |null                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                

|WOS:000441443500004|Journal|2018|1557-9964|1545-5963|10.1109/TCBB.2017.2780106         |A Sparse Regression Method for Group-Wise Feature Selection with False Discovery Rate Control                                                                                                             |IEEE-ACM TRANSACTIONS ON COMPUTATIONAL BIOLOGY AND BIOINFORMATICS|IEEE COMPUTER SOC            |The authors would like to thank Malgorzata Bogdan and Weiji Su for sharing their results with us and for helpful discussion. They would also like to thank Wei Zhu for the lookup of GEFOS-seq p-values. A.G., S.C., and Y.-P.W. were partially supported by NIH (R01 GM109068, R01 MH104680, R01 MH107354) and NSF (#1539067). D.B. acknowledges the support from NIMH grant R01MH108467.                                                                                                                                                                                                                                          

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [71]:
import org.apache.spark.sql.SaveMode

//val WoSIU8 = WoSIU7.filter($"PU".contains("ELSEVIER"))
//WoSIU8.describe().filter($"summary" === "count").show
WoSIU9.select("WoSid","PT","PY","EI","SN","DI","TI","SO","PU","FX","RPcount","RPnames","RP","AU","RPflags","AU-C1-map","C1")
    .coalesce(1).write.mode(SaveMode.Overwrite).format("com.databricks.spark.csv")
    .option("header", "true")
    .option("codec", "org.apache.hadoop.io.compress.GzipCodec")
    .save("/WoSraw/WoS2019/IUpapersExtract")

In [69]:
WoSIU9.show(false)
//.withColumn("RPnames", array_join($"RPnameList.last_name", "|"))

+-------------------+-------+----+---------+---------+----------------------------------+----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+-----------------------------------------------------------------+-----------------------------+------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

|WOS:000414522900001|Journal|2018|1557-9042|0897-7151|10.1089/neu.2017.5203             |Traumatic Brain Injury in hTau Model Mice: Enhanced Acute Macrophage Response and Altered Long-Term Recovery                                                                                              |JOURNAL OF NEUROTRAUMA                                           |MARY ANN LIEBERT, INC        |This work was supported by the Department of Defense and National Institutes of Health (W81XWH-12-1-0629, BTL; R21NS077089, R01NS083704, R21NS093442, K.B.). We thank the Rodent Behavioral Core and the Flow Cytometry Core at the Lerner Research Institute within the Cleveland Clinic for technical advice and support. We thank Dr. Imad Najm for use of the fluid percussion device. Author contributions: O.K-C. designed, performed, and analyzed all experiments and wrote the manuscript; M.S. performed surgeries, TBIs, and flow cytometry experiments; S.P. analyzed all flow cytometry data and assisted in interpreta

|WOS:000418128000001|Journal|2018|1557-9042|0897-7151|10.1089/neu.2017.5376             |Acute Changes in Plasma Total Tau Levels Are Independent of Subconcussive Head Impacts in College Football Players                                                                                        |JOURNAL OF NEUROTRAUMA                                           |MARY ANN LIEBERT, INC        |This work was supported by the Pennsylvania Athletic Trainers' Society research grant (to K. Kawata), generous support from Athole G. Jacobi, MD, and the Marianne Garman Burton Foundation for Caregivers (to D. Langford), and a seed grant from Temple University Office of the Vice Provost for Research (to D. Langford). Sponsors had no role in the design or execution of the study; collection, management, analysis, or interpretation of the data; preparation, review, or approval of the manuscript; or decision to submit the manuscript for publication.                                                             

|WOS:000439102000002|Journal|2018|1526-632X|0028-3878|10.1212/WNL.0000000000005213      |Attention-deficit/hyperactivity disorder medication and seizures                                                                                                                                          |NEUROLOGY                                                        |LIPPINCOTT WILLIAMS & WILKINS|This project was supported by NIMH grant R01MH102221, NIH grant T32HD07475, and NIDA grant K99DA040727. MarketScan is a registered trademark of Truven Health Analytics Inc.                                                                                                                                                                                                                                                                                                                                                                                                                                                        

|WOS:000436794300577|Journal|2018|1530-0293|0090-3493|10.1097/01.ccm.0000528630.37152.3a|ACUTE MASSIVE LOWER GASTROINTESTINAL HEMORRHAGE: A RARE PRESENTATION OF DISSEMINATED TUBERCULOSIS                                                                                                         |CRITICAL CARE MEDICINE                                           |LIPPINCOTT WILLIAMS & WILKINS|null                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                

...

|WOS:000445616200003|Journal|2018|1469-7610|0021-9630|10.1111/jcpp.12975                |A longitudinal, within-person investigation of the association between the P3 ERP component and externalizing behavior problems in young children                                                         |JOURNAL OF CHILD PSYCHOLOGY AND PSYCHIATRY                       |WILEY                        |The Toddler Development Study was funded by Grant HD073202 from the Eunice Kennedy Shriver National Institute of Child Health and Human Development. IP was supported by a National Research Service Award from the National Institute of Mental Health (1F31MH100814-01A1). The authors have declared that they have no competing or potential conflicts of interest.                                                                                                                                                                                                                                                              

|WOS:000419938200004|Journal|2018|1558-7967|0001-4826|10.2308/accr-51842                |Clarity Begins at Home: Internal Information Asymmetry and External Communication Quality                                                                                                                 |ACCOUNTING REVIEW                                                |AMER ACCOUNTING ASSOC        |We gratefully acknowledge the financial support provided by the General Research Fund of Hong Kong Research Grants Council (Project No. 792813).                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

|WOS:000438114500005|Journal|2018|1434-6052|1434-6044|10.1140/epjc/s10052-018-5995-6    |Search for heavy particles decaying into top-quark pairs using lepton-plus-jets events in proton-proton collisions at root s=13 TeV with the ATLAS detector                                               |EUROPEAN PHYSICAL JOURNAL C                                      |SPRINGER                     |We thank CERN for the very successful operation of the LHC, as well as the support staff from our institutions without whom ATLAS could not be operated efficiently. We acknowledge the support of ANPCyT, Argentina; YerPhI, Armenia; ARC, Australia; BMWFW and FWF, Austria; ANAS, Azerbaijan; SSTC, Belarus; CNPq and FAPESP, Brazil; NSERC, NRC and CFI, Canada; CERN; CONICYT, Chile; CAS, MOST and NSFC, China; COLCIENCIAS, Colombia; MSMT CR, MPO CR and VSC CR, Czech Republic; DNRF and DNSRC, Denmark; IN2P3-CNRS, CEA-DRF/IRFU, France; SRNSFG, Georgia; BMBF, HGF, and MPG, Germany; GSRT, Greece; RGC, Hong Kong SAR, 

|WOS:000449567500007|Journal|2018|1740-634X|0893-133X|10.1038/s41386-018-0166-x         |Striatal activity correlates with stimulant-like effects of alcohol in healthy volunteers                                                                                                                 |NEUROPSYCHOPHARMACOLOGY                                          |NATURE PUBLISHING GROUP      |This research was supported by the National Institute on Alcohol Abuse and Alcoholism Grant R21 AA017502 (E.C.). J.W. was supported by National Institute on Alcohol Abuse and Alcoholism Grant K01 AA024519. T.J.R. and E.A.S. were supported by the National Institute on Drug Abuse Intramural Research Program. S.O. was supported by National Institute on Alcohol Abuse and Alcoholism grant P60 AA007611. The funding agencies had no involvement in the research other than financial support.                                                                                                                              

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [57]:
WoSIU7.printSchema

root
 |-- UID: string (nullable = true)
 |-- _pubtype: string (nullable = true)
 |-- _pubyear: long (nullable = true)
 |-- fund_text: struct (nullable = true)
 |    |-- p: array (nullable = true)
 |    |    |-- element: string (containsNull = true)
 |-- titles: struct (nullable = true)
 |    |-- _count: long (nullable = true)
 |    |-- title: array (nullable = true)
 |    |    |-- element: struct (containsNull = true)
 |    |    |    |-- _VALUE: string (nullable = true)
 |    |    |    |-- _translated: string (nullable = true)
 |    |    |    |-- _type: string (nullable = true)
 |-- reprint_addresses: struct (nullable = true)
 |    |-- _count: long (nullable = true)
 |    |-- address_name: array (nullable = true)
 |    |    |-- element: struct (containsNull = true)
 |    |    |    |-- address_spec: struct (nullable = true)
 |    |    |    |    |-- _addr_no: long (nullable = true)
 |    |    |    |    |-- city: string (nullable = true)
 |    |    |    |    |-- country: string (nullable 

In [55]:
//WoSIU8.select("RPflag").withColumn("RPflagN", explode($"RPflag")).withColumn("RPflags", array_join($"RPflagN", "|")).show

/*
val defaultStr = "N"

def patchNull(default: String) = {
  udf((row: Seq[Row]) =>
    row.map(r => (r.getAs[String](0)) match {
      case "" => default
      case e => e
    }
  ) )
}

val WoSIU8b = WoSIU8.withColumn("RPflagN", patchNull(defaultStr)($"RPflag"))//.na.fill(defaultStr)
      //.withColumn("C1flagN", patchNull(defaultStr)($"C1flag")).na.fill(defaultStr)
WoSIU8b.show(false)
*/
WoSIU7.show(false)

+-------------------+--------+--------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

|UID                |_pubtype|_pubyear|fund_text                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

+-------------------+--------+--------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

|WOS:000418232300001|Journal |2018    |[[We thank Drs. Kenneth Cornetta and Aaron Shaw (IU School of Medicine) and Dirk Lindemann (Technische Universitat Dresden) for providing plasmids for lentiviral vector production, Drs. David Gilley, Scott Witting, and Kenneth Cornetta (IU School of Medicine) for providing cell lines, Dr. Helmut Hanenberg (Heinrich Heine Universitat Dusseldorf) for plasmids and advice on the use of RetroNectin for lentiviral vector transduction and Dr. Alfred Lewin (University of Florida) for help with the SOD2 knockdown mouse model. This paper was previously submitted as part of the graduation requirements for a PhD at Indiana University undertaken by S.L.P. This research was supported by the NIH (EY023629), NEI Core grant P30 EY03039, BrightFocus (M2009024), and an unrestricted grant from Research to Prevent Blindness.]]                                                                                                                                                

|WOS:000414522900001|Journal |2018    |[[This work was supported by the Department of Defense and National Institutes of Health (W81XWH-12-1-0629, BTL; R21NS077089, R01NS083704, R21NS093442, K.B.). We thank the Rodent Behavioral Core and the Flow Cytometry Core at the Lerner Research Institute within the Cleveland Clinic for technical advice and support. We thank Dr. Imad Najm for use of the fluid percussion device. Author contributions: O.K-C. designed, performed, and analyzed all experiments and wrote the manuscript; M.S. performed surgeries, TBIs, and flow cytometry experiments; S.P. analyzed all flow cytometry data and assisted in interpretation of results; S.B. performed silver staining and assisted with biochemical analysis of data; A.K. performed immunohistochemistry and assisted with data analysis; Y-S.L. provided expertise in use of the fluid percussion device and analysis of data. K.B. provided expertise in use of the hTau mouse model and analysis of data; R.M.R. provided fun

...

|WOS:000417301100001|Journal |2018    |[[Project supported by the first author's doctoral scholarships/fellowships: American Cancer Society Doctoral Scholarship in Cancer Nursing (DSCN-05-181-01); Individual National Research Service Award, (F31NR009733); Institutional National Research Service Award (T32 NR007066); Mary Margaret Walther Cancer Institute Pre-Doctoral Fellowship; and a Research Incentive Fellowship (Indiana University School of Nursing).]]                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             

|WOS:000418128000001|Journal |2018    |[[This work was supported by the Pennsylvania Athletic Trainers' Society research grant (to K. Kawata), generous support from Athole G. Jacobi, MD, and the Marianne Garman Burton Foundation for Caregivers (to D. Langford), and a seed grant from Temple University Office of the Vice Provost for Research (to D. Langford). Sponsors had no role in the design or execution of the study; collection, management, analysis, or interpretation of the data; preparation, review, or approval of the manuscript; or decision to submit the manuscript for publication.]]                                                                                                                                                                                                                                                                                                                                                                                                                      

|WOS:000414274200002|Journal |2018    |null                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             

|WOS:000468819503111|Journal |2018    |null                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [64]:
WoSIU7.printSchema

root
 |-- UID: string (nullable = true)
 |-- _pubtype: string (nullable = true)
 |-- _pubyear: long (nullable = true)
 |-- fund_text: struct (nullable = true)
 |    |-- p: array (nullable = true)
 |    |    |-- element: string (containsNull = true)
 |-- titles: struct (nullable = true)
 |    |-- _count: long (nullable = true)
 |    |-- title: array (nullable = true)
 |    |    |-- element: struct (containsNull = true)
 |    |    |    |-- _VALUE: string (nullable = true)
 |    |    |    |-- _translated: string (nullable = true)
 |    |    |    |-- _type: string (nullable = true)
 |-- reprint_addresses: struct (nullable = true)
 |    |-- _count: long (nullable = true)
 |    |-- address_name: array (nullable = true)
 |    |    |-- element: struct (containsNull = true)
 |    |    |    |-- address_spec: struct (nullable = true)
 |    |    |    |    |-- _addr_no: long (nullable = true)
 |    |    |    |    |-- city: string (nullable = true)
 |    |    |    |    |-- country: string (nullable 

lastException: Throwable = null
